# FTX reader

In [1]:
import matplotlib
%matplotlib inline
import cufflinks as cf
cf.go_offline()
cf.set_config_file(offline=False, world_readable=True)
import plotly.express as px

import sys
sys.path.append('../')
from history_script import *

import os
directory='C:/Users/david/puffin/DerivativeArbitrage/Runtime/live_parquets/'
end_time=datetime.now()#.replace(minute=0,second=0,microsecond=0)
start_time=datetime(2021,12,2)#end_time-timedelta(hours=1)
halflife=timedelta(seconds=1)
modes=[('h','high'),('c','close'),('l','low')]
coins=['SXP']

read static_params


C:\Users\david\Puffin\DerivativeArbitrage\ftx_portfolio.py:594: FutureWarning:

Could not cast to float64, falling back to object. This behavior is deprecated. In a future version, when a dtype is passed to 'DataFrame', either all columns will be cast to that dtype, or a TypeError will be raised

C:\Users\david\Puffin\DerivativeArbitrage\ftx_portfolio.py:586: FutureWarning:

Could not cast to float64, falling back to object. This behavior is deprecated. In a future version, when a dtype is passed to 'DataFrame', either all columns will be cast to that dtype, or a TypeError will be raised

C:\Users\david\Puffin\DerivativeArbitrage\ftx_portfolio.py:587: FutureWarning:

Could not cast to float64, falling back to object. This behavior is deprecated. In a future version, when a dtype is passed to 'DataFrame', either all columns will be cast to that dtype, or a TypeError will be raised



In [2]:
futures_df=ftx_history(dirname='',start=start_time,end=end_time,timeframe='1m',coin_list=coins)

C:\Users\david\Puffin\DerivativeArbitrage\JupyterNotebooks\..\history_script.py:40: FutureWarning:

Could not cast to float64, falling back to object. This behavior is deprecated. In a future version, when a dtype is passed to 'DataFrame', either all columns will be cast to that dtype, or a TypeError will be raised



funding_history: SXP-PERP
rate_history: SXP-PERP


C:\Users\david\Puffin\DerivativeArbitrage\JupyterNotebooks\..\ftx_history.py:24: FutureWarning:

Could not cast to float64, falling back to object. This behavior is deprecated. In a future version, when a dtype is passed to 'DataFrame', either all columns will be cast to that dtype, or a TypeError will be raised



rate_history: SXP-1231
price_history: SXP/USD
borrow_history: SXP
borrow_history: USD


### rates markets

In [3]:
prices=futures_df[[c for c in futures_df.columns if any(string in c for string in ['price/c'])]]

short_rates=futures_df[[c for c in futures_df.columns if any(string in c for string in ['PERP/rate/c','rate/borrow'])]]
short_rates=short_rates.ewm(halflife=halflife,times=short_rates.index).mean()

long_rates=futures_df[[c for c in futures_df.columns if all(['/rate/c' in c,not ('PERP' in c)])]]
long_rates=long_rates

for c in coins:
    short_rates[c+'/long_perp_carry']=short_rates[c+'-PERP/rate/c']-short_rates['USD/rate/borrow']
    short_rates[c+'/short_perp_carry']=-short_rates[c+'-PERP/rate/c']-short_rates[c+'/rate/borrow']
    long_rates[c+'/long_future_carry']=long_rates[c+'-1231/rate/c']-short_rates['USD/rate/borrow']
    long_rates[c+'/short_future_carry']=-long_rates[c+'-1231/rate/c']-short_rates[c+'/rate/borrow']

pd.concat([prices,short_rates,long_rates],axis=0).iplot(secondary_y=list(short_rates.columns)+list(long_rates.columns))

### carry

In [4]:
pd.concat([prices,short_rates.filter(like='carry')],axis=0).iplot(secondary_y=list(prices.columns))

# stopout: show min/max of premiums

In [5]:
end_time=datetime.now()#.replace(minute=0,second=0,microsecond=0)
start_time=end_time-timedelta(hours=1)
granular_df=ftx_history(dirname='',start=start_time,end=end_time,timeframe='15s',coin_list=coins)

funding_history: SXP-PERP
rate_history: SXP-PERP
rate_history: SXP-1231
price_history: SXP/USD
borrow_history: SXP
borrow_history: USD


In [6]:
def compute_premium(df: pd.DataFrame,mode=1) -> pd.Series:
    return (df.filter(like='/mark/'+ modes[mode][0]).iloc[:,0]/df.filter(like='/indexes/'+modes[mode][1]).iloc[:,0]-1)*10000
def compute_premium_vs_spot(df: pd.DataFrame,mode=1) -> pd.Series:
    return (df.filter(like='/mark/'+ modes[mode][0]).iloc[:,0]/df.filter(like='/price/'+modes[mode][0]).iloc[:,0]-1)*10000
def compile_list(premium_list: list) -> pd.DataFrame:
    premium=premium_list[0]
    for df in premium_list[1:]:
        premium=premium.join(df,how='outer')
    return premium[~premium.index.duplicated()]

In [7]:
granular_df['premium']=compute_premium_vs_spot(granular_df)
prices=granular_df[[c+'/price/c' for c in coins]]
granular_df[['premium']].iplot()

In [8]:
premium=compute_premium(granular_df,mode=0)
ewMax=premium.resample('1h').max()
ewMax=ewMax[~ewMax.index.duplicated()]
pd.concat([prices,ewMax],axis=0).iplot(secondary_y=list(prices.columns))

In [9]:
premium=compute_premium(granular_df,mode=2)
ewMin=premium.resample('1h').min()
ewMin=ewMin[~ewMin.index.duplicated()]
pd.concat([prices,ewMin],axis=0).iplot(secondary_y=list(prices.columns))